In [1]:
pip install pandas openpyxl xlsxwriter matplotlib

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [12]:
import os
import pandas as pd
from openpyxl import load_workbook
from openpyxl.utils import get_column_letter
from openpyxl.chart import (
    PieChart,
    BarChart,
    Reference,
)
from openpyxl.chart.label import DataLabelList

# Define the directory containing the trial sheets
directory = r'C:\Users\ctr22\Downloads\RAMPatientQuestions'
output_file = os.path.join(directory, 'main.xlsx')

# Function to convert column number to Excel column letters
def get_excel_column_letter(n):
    string = ""
    while n > 0:
        n, remainder = divmod(n - 1, 26)
        string = chr(65 + remainder) + string
    return string

# Function to process each trial sheet and update the main DataFrame
def process_trial_sheet(trial_path, main):
    try:
        # Read the specified sheet, treating "N/A" and "None" as valid text
        trial = pd.read_excel(trial_path, sheet_name='Answer Counts (DNP)', keep_default_na=False, na_values=[])
    except ValueError as e:
        print(f"Error reading '{trial_path}': {e}")
        return main
    except FileNotFoundError as e:
        print(f"File not found: '{trial_path}'. Skipping.")
        return main
    
    # Print the first few rows to ensure the file is read correctly
    print(f"Processing {trial_path}")
    print(trial.head())

    if trial.empty:
        print(f"No data found in '{trial_path}'. Skipping processing.")
        return main
    
    if trial.shape[1] < 3:
        print(f"Error: '{trial_path}' does not have enough columns.")
        return main
    
    for index, trial_row in trial.iterrows():
        if len(trial_row) < 3:
            print(f"Skipping row in '{trial_path}': Insufficient columns.")
            continue
        
        cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]
        
        # Check if there's already a matching row in main
        match = main[(main['Cell1'] == cell1) & (main['Cell2'] == cell2)]
        
        if not match.empty:
            # If there's a match, update the existing row
            main_index = match.index[0]  # Use match.index[0] safely here
            print(f"Match found for Cell1: {cell1}, Cell2: {cell2} at index {main_index}")
            main.at[main_index, trial_path] = cell3
        else:
            # If there's no match, add a new row to main
            print(f"No match found for Cell1: {cell1}, Cell2: {cell2}. Adding new row.")
            new_row = pd.DataFrame({'Cell1': [cell1], 'Cell2': [cell2], 'Sum': [0], trial_path: [cell3]})
            main = pd.concat([main, new_row], ignore_index=True)

    # Update the 'Sum' column after processing all trial sheets
    for i in range(len(main)):
        col_count = len(main.columns)
        if col_count > 3:
            col_letter = get_excel_column_letter(col_count)
            # Sum numeric values only in columns starting from index 3
            sum_value = main.iloc[i, 3:].apply(pd.to_numeric, errors='coerce').sum()
            main.at[i, 'Sum'] = sum_value

    return main

# Function to add charts to a worksheet
def add_charts_to_worksheet(workbook, sheet_name, data):
    worksheet = workbook[sheet_name]
    chart_row_start = 2  # Start row for charts
    chart_col_start = len(data.columns) + 3  # Start column for charts

    # Iterate through each group in data to create charts
    for cell1_value, group_data in data.groupby('Cell1'):
        num_rows = len(group_data)

        # Skip groups with fewer than 2 rows (cannot create meaningful chart)
        if num_rows < 2:
            continue

        chart_end_row = chart_row_start + num_rows

        # Initialize chart variable
        chart = None

        # Add pie chart for groups with less than 5 rows
        if num_rows < 5:
            chart = PieChart()
            labels = Reference(worksheet, min_col=2, min_row=chart_row_start, max_row=chart_end_row)
            chart_row_start -=1
            chart_end_row -=1
            data_ref = Reference(worksheet, min_col=3, min_row=chart_row_start, max_row=chart_end_row)
            chart_row_start +=1
            chart_end_row +=1
            chart.add_data(data_ref, titles_from_data=True)
            chart.set_categories(labels)
            chart.title = f'Pie Chart for {cell1_value}'
            chart.legend.position = 'r'

        else:
            # Add column chart for groups with 5 or more rows
            chart = BarChart()
            labels = Reference(worksheet, min_col=2, min_row=chart_row_start, max_row=chart_end_row)
            chart_row_start -=1
            chart_end_row -=1
            data_ref = Reference(worksheet, min_col=3, min_row=chart_row_start, max_row=chart_end_row)
            chart_row_start +=1
            chart_end_row +=1
            chart.add_data(data_ref, titles_from_data=True)
            chart.set_categories(labels)
            chart.title = f'Column Chart for {cell1_value}'
            chart.legend.position = 'r'

        if chart:
            # Insert chart into Sheet1
            worksheet.add_chart(chart, f'{get_column_letter(chart_col_start)}{chart_row_start}')

        # Increment chart start row for the next group
        chart_row_start += num_rows

# Function to update the master DataFrame
def update_master_df(master_df, subfolder_df):
    for _, row in subfolder_df.iterrows():
        cell1, cell2, cell3 = row['Cell1'], row['Cell2'], row['Sum']
        match = master_df[(master_df['Cell1'] == cell1) & (master_df['Cell2'] == cell2)]

        if not match.empty:
            master_index = match.index[0]
            master_df.at[master_index, 'Sum'] += cell3
        else:
            new_row = pd.DataFrame({'Cell1': [cell1], 'Cell2': [cell2], 'Sum': [cell3]})
            master_df = pd.concat([master_df, new_row], ignore_index=True)

    return master_df

# Initialize the master DataFrame
master_main = pd.DataFrame(columns=['Cell1', 'Cell2', 'Sum'])

# Check if the directory exists
if not os.path.isdir(directory):
    print(f"The directory {directory} does not exist.")
else:
    # Iterate through all subdirectories and files
    with pd.ExcelWriter(output_file, engine='openpyxl', mode='w') as writer:
        for subdir, _, files in os.walk(directory):
            subfolder_name = os.path.basename(subdir)
            main = pd.DataFrame(columns=['Cell1', 'Cell2', 'Sum'])
            
            for filename in files:
                if filename.endswith('.xlsx'):
                    trial_path = os.path.join(subdir, filename)
                    main = process_trial_sheet(trial_path, main)
            
            if not main.empty:
                # Remove rows where 'Cell2' is blank
                main = main[main['Cell2'] != ""]
                # Remove rows where 'Sum' is zero
                main = main[main['Sum'] != 0]
                # Sort the main DataFrame by the first column in alphabetical order
                main.sort_values(by='Cell1', inplace=True)

                # Write the subfolder DataFrame to the Excel file
                main.to_excel(writer, index=False, sheet_name=subfolder_name)
                workbook = writer.book
                
                # Add charts to the subfolder worksheet
                add_charts_to_worksheet(workbook, subfolder_name, main)
                
                # Update the master DataFrame
                master_main = update_master_df(master_main, main)
        
        if not master_main.empty:
            # Remove rows where 'Cell2' is blank
            master_main = master_main[master_main['Cell2'] != ""]
            # Remove rows where 'Sum' is zero
            master_main = master_main[master_main['Sum'] != 0]
            # Sort the master DataFrame by the first column in alphabetical order
            master_main.sort_values(by='Cell1', inplace=True)

            # Write the master DataFrame to the Excel file
            master_main.to_excel(writer, index=False, sheet_name='Master')
            workbook = writer.book
            
            # Add charts to the master worksheet
            add_charts_to_worksheet(workbook, 'Master', master_main)

    print(f"The file with charts has been created at {output_file}")


Error reading 'C:\Users\ctr22\Downloads\RAMPatientQuestions\main.xlsx': Excel file format cannot be determined, you must specify an engine manually.
Processing C:\Users\ctr22\Downloads\RAMPatientQuestions\2016\Alamo_2016_Clinic Overview Report copy.xlsx
                       Question                    Answer  \
0  dummy question DO NOT DELETE  NULL Value DO NOT Delete   
1  dummy question DO NOT DELETE  NULL Value DO NOT Delete   
2  dummy question DO NOT DELETE  NULL Value DO NOT Delete   
3  dummy question DO NOT DELETE  NULL Value DO NOT Delete   
4                     Ethnicity                  Hispanic   

                  AnsText  AnsCount  TotalAns   Percent  Q#  EventID     Event  
0                               319       322  0.990683  18     1045  Alamo TX  
1             128 St John         1       322  0.003106  18     1045  Alamo TX  
2  erickasosa19@gmail.com         1       322  0.003106  18     1045  Alamo TX  
3    Mshtiva101@gmail.com         1       322  0.003106

C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]
C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]
C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by 

Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO NOT DELETE, Cell2: NULL Value DO NOT Delete at index 0
Match found for Cell1: dummy question DO

C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]
C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]
C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by 

No match found for Cell1: Height, Cell2: 5' 8'. Adding new row.
No match found for Cell1: Height, Cell2: 5' 9'. Adding new row.
No match found for Cell1: Height, Cell2: 6' 0'. Adding new row.
No match found for Cell1: Height, Cell2: 6' 1'. Adding new row.
No match found for Cell1: Height, Cell2: 6' 2'. Adding new row.
No match found for Cell1: Height, Cell2: 6' 3'. Adding new row.
No match found for Cell1: Height, Cell2: 6' 4'. Adding new row.
No match found for Cell1: Height, Cell2: 6' 6'. Adding new row.
No match found for Cell1: Height, Cell2: Less than 4'. Adding new row.
Match found for Cell1: Height, Cell2: No Answer at index 6
No match found for Cell1: Height, Cell2: Young Child. Adding new row.
Match found for Cell1: Household Size, Cell2: 1 at index 7
Match found for Cell1: Household Size, Cell2: 10+ at index 8
Match found for Cell1: Household Size, Cell2: 2 at index 9
Match found for Cell1: Household Size, Cell2: 3 at index 10
Match found for Cell1: Household Size, Cell2: 4 a

...

Processing C:\Users\ctr22\Downloads\RAMPatientQuestions\2024\Sharon, PA 2024 One Pager copy.xlsx
       Answer Counts  Unnamed: 1 Unnamed: 2 Unnamed: 3 Unnamed: 4 Unnamed: 5  \
0           Question      Answer   AnsCount   TotalAns    Percent      XQKey   
1  AlternateEmerRoom  Don't know          2        285   0.007018        101   
2  AlternateEmerRoom          No         87        285   0.305263        101   
3  AlternateEmerRoom     Refused          8        285    0.02807        101   
4  AlternateEmerRoom         Yes        188        285   0.659649        101   

  Unnamed: 6  Unnamed: 7  
0   XEventID       Event  
1       1554  Sharon2024  
2       1554  Sharon2024  
3       1554  Sharon2024  
4       1554  Sharon2024  
Match found for Cell1: Question, Cell2: Answer at index 178
Match found for Cell1: AlternateEmerRoom, Cell2: Don't know at index 0
Match found for Cell1: AlternateEmerRoom, Cell2: No at index 1
Match found for Cell1: AlternateEmerRoom, Cell2: Refused at index 

C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]
C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]


Processing C:\Users\ctr22\Downloads\RAMPatientQuestions\2024\St. Thomas, USVI 2024 One Pager copy.xlsx
       Answer Counts Unnamed: 1 Unnamed: 2 Unnamed: 3 Unnamed: 4 Unnamed: 5  \
0           Question     Answer   AnsCount   TotalAns    Percent      XQKey   
1  AlternateEmerRoom    Refused          1          1          1        101   
2          Ethnicity    Refused          1          1          1         12   
3    HealthInsurance    Refused          1          1          1         97   
4            HowHear    Refused          1          1          1          9   

  Unnamed: 6  Unnamed: 7  
0   XEventID       Event  
1       1625  StThoIRT24  
2       1625  StThoIRT24  
3       1625  StThoIRT24  
4       1625  StThoIRT24  
Match found for Cell1: Question, Cell2: Answer at index 178
Match found for Cell1: AlternateEmerRoom, Cell2: Refused at index 2
Match found for Cell1: Ethnicity, Cell2: Refused at index 27
Match found for Cell1: HealthInsurance, Cell2: Refused at index 52
Matc

C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]
C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell1, cell2, cell3 = trial_row[0], trial_row[1], trial_row[2]
C:\Users\ctr22\AppData\Local\Temp\ipykernel_91384\2867033703.py:53: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by 

Match found for Cell1: Military, Cell2: Never in Military at index 88
Match found for Cell1: Military, Cell2: Refused at index 89
Match found for Cell1: Military, Cell2: Veteran at index 91
Match found for Cell1: Ramclinics, Cell2: None at index 98
Match found for Cell1: ReasonforRAM, Cell2: Availability of Service at index 100
Match found for Cell1: ReasonforRAM, Cell2: Don't know at index 183
Match found for Cell1: ReasonforRAM, Cell2: Free at index 101
Match found for Cell1: ReasonforRAM, Cell2: Other at index 102
Match found for Cell1: ReasonforRAM, Cell2: Proximity at index 103
Match found for Cell1: ReasonforRAM, Cell2: Quality of Service at index 104
Match found for Cell1: ReasonforRAM, Cell2: Refuse at index 105
Match found for Cell1: SurveyType, Cell2: Either way is fine at index 106
Match found for Cell1: SurveyType, Cell2: Email at index 107
Match found for Cell1: SurveyType, Cell2: N/A at index 108
Match found for Cell1: SurveyType, Cell2: Text Message at index 109
Match fo